In [1]:
import pandas as pd
from splycer.blocker import BlockDB
from splycer.record_set import RecordDB
from splycer.pairs_set import PairsDB
from splycer.feature_engineer import FeatureEngineer
import recordlinkage as rl
import pyodbc
import numpy as np
from xgboost import XGBClassifier
from sklearn.metrics import confusion_matrix, precision_score, recall_score
import pickle as pkl
from tqdm import tqdm

import turbodbc
conn = turbodbc.connect('rec_db')

In [2]:
# Load the model
modelPath = r'R:\JoePriceResearch\record_linking\projects\deep_learning\paper_RR\CensusTree_2020\final\3-train_models\model_1900_1910.dat'
model = pkl.load(open(modelPath, "rb"))


In [3]:
extra_join = ''
sql1910 = RecordDB('compiled_1910','index','rec_db',extra_joins=extra_join)
sql1920 = RecordDB('compiled_1920','index','rec_db',extra_joins=extra_join)

def run( outfile, chunksize=1000000, logfile='log5.txt'):
    """Run the model on the full compare set, writing results to file."""
    with tqdm(total=blocked_pairs.ncompares) as pbar: # create loading bar to save comparisons
        print("start tqdm")
        
        print("getting chunk")
        for cand_mat in blocked_pairs.get_pairs(chunksize=chunksize): # iterate through blocked comparisons
            print("Get new chunk.")
            try:
                pairs = pd.MultiIndex.from_arrays((cand_mat[0],cand_mat[1])) # store blocked pairs in pandas multiindex
                
                print("debugging records getting.")
                np.unique(cand_mat[0])
                print(np.unique(cand_mat[0]))
                print("getting records (This takes the longest.)")
                rec1 = sql1910.get_records(np.unique(cand_mat[0])).set_index('index') # pull census field data from sql
                rec2 = sql1920.get_records(np.unique(cand_mat[1])).set_index('index')
                
                print("computing records")
                comp_vecs = c.compute(pairs, rec1, rec2)
                comp_vecs.columns=['res','bp','first_jaro','last_jaro','birth_year','immigration','first_comm',
           'last_comm','marstat','mbp','fbp','rel']
                
                print("predicting")
                preds = model.predict_proba(comp_vecs) # predict matches with model
                print("Done predicting")
                # column output of below line of code: index1, index2, link_prob

                data = pd.DataFrame({'index1910':cand_mat[0],'index1920':cand_mat[1],'link_prob':preds[:,1]})
                print("saving")
                data.to_csv(outfile,mode='a',header=None,index=False)
                pbar.update(chunksize)
                print("Done saving")
            except ValueError:
                print("exception")
                with open(logfile, "a") as l:
                    l.write(f'failed to compile data for indices {cand_mat[0][0]} to {cand_mat[0][-1]}\n')
                pbar.update(chunksize)    
            print("getting new chunk")
    print("Linking completed")

In [4]:
from recordlinkage.base import BaseCompareFeature

class eucledian_distance(BaseCompareFeature):
    def __init__(self, left_on, right_on):
        super(eucledian_distance, self).__init__(left_on, right_on)
        self.n = len(left_on)
    def _compute_vectorized(self,*args):
        s1 = args[:self.n]
        s2 = args[self.n:]
        return np.linalg.norm(np.array(s1)-np.array(s2),ord=2,axis=0)
    
class commonality_weight(BaseCompareFeature):
    def __init__(self,left_on,right_on):
        super(commonality_weight, self).__init__(left_on, right_on)
    def _compute_vectorized(self,s1,s2):
        return 1 / np.log1p((s1 + s2) / 2)
    
def get_compare_engine(drop=[]):
    exact_match_features = ['marstat','mbp','fbp','rel','first_nysiis','last_nysiis']
    exact_match_features = [feat for feat in exact_match_features if feat not in drop]
    c = rl.Compare() # declare comparison object
    if 'res' not in drop:
        c.geo('res_lat','res_lon','res_lat','res_lon',method = 'exp',scale=500)
    if 'bp' not in drop:
        c.geo('bp_lat','bp_lon','bp_lat','bp_lon', method = 'exp',scale=500)
    if 'first_jaro' not in drop:
        c.string('first','first',method = 'jarowinkler')
    if 'last_jaro' not in drop:
        c.string('last','last', method = 'jarowinkler')
    #c.string('first','first',method = 'qgram')
    #c.string('last','last', method = 'qgram')
    if 'birth_year' not in drop:
        c.numeric('birth_year','birth_year', method = 'lin', scale = 1, offset = 1)
    if 'immigration' not in drop:
        c.numeric('immigration','immigration', method = 'lin', scale = 1, offset = 1)
    
    vec_cols = [f'occ_vec{i}' for i in range(128)]
    if 'occ' not in drop:
        c.add(eucledian_distance(vec_cols,vec_cols))
    if 'comm_first' not in drop:
        c.add(commonality_weight('first_comm','first_comm'))
    if 'comm_last' not in drop:
        c.add(commonality_weight('last_comm','last_comm'))    
    for col in exact_match_features:
        c.exact(col,col)
    return c

c = get_compare_engine(drop=['occ','first_nysiis','last_nysiis'])

In [5]:
blocked_pairs = PairsDB('compares_1910_1920',['index1910','index1920'],'rec_db')
savePath = r"R:\JoePriceResearch\record_linking\projects\deep_learning\paper_RR\CensusTree_2020\final\4-predict\predictions_1900_1910.csv"
run(savePath)

  0%|                                                                        | 0/292652792 [00:00<?, ?it/s]

start tqdm
getting chunk
Get new chunk.
debugging records getting.
[79984071 79984078 79984088 ... 84674384 84674387 84674388]
getting records (This takes the longest.)
doing the expand_dims, dropping table.
Done expanding dims
here in record_set.py


  0%|                                                                        | 0/292652792 [00:23<?, ?it/s]


KeyboardInterrupt: 

In [7]:
for i in blocked_pairs:
    print(i)

(23813031, 79984071)
(22027618, 79984078)
(28541227, 79984078)
(23279977, 79984088)
(26506800, 79984088)
(29656387, 79984098)
(27598050, 79984124)
(24668991, 79984140)
(21533946, 79984144)
(21370604, 79984146)
(22925079, 79984167)
(23042639, 79984174)
(27673776, 79984174)
(26700529, 79984188)
(21181920, 79984202)
(20221084, 79984204)
(20851958, 79984204)
(20958787, 79984204)
(28192630, 79984204)
(28518875, 79984204)
(20239509, 79984220)
(23659426, 79984220)
(29868803, 79984228)
(22854858, 79984239)
(21607395, 79984242)
(22495096, 79984242)
(23663263, 79984242)
(24043769, 79984242)
(29178410, 79984243)
(29455055, 79984243)
(29646719, 79984244)
(29691480, 79984244)
(29763804, 79984244)
(29991299, 79984244)
(22265616, 79984246)
(23714901, 79984246)
(24540104, 79984246)
(21950991, 79984252)
(22154009, 79984252)
(22495286, 79984252)
(24731606, 79984252)
(22498860, 79984254)
(21043530, 79984270)
(21960992, 79984270)
(23878638, 79984270)
(24802794, 79984270)
(24882608, 79984270)
(22686592, 79

(23653016, 79994938)
(26971302, 79994938)
(28240938, 79994956)
(27958073, 79994961)
(29506846, 79994976)
(28417288, 79994980)
(20474678, 79994983)
(22467546, 79994985)
(22552072, 79994985)
(22848532, 79994985)
(24015980, 79994985)
(24756815, 79994985)
(22314013, 79994989)
(20239555, 79994990)
(23249110, 79994990)
(23676783, 79994990)
(26161665, 79994990)
(26962715, 79994990)
(20661904, 79994999)
(21852640, 79994999)
(27190713, 79994999)
(27857554, 79994999)
(20481268, 79995001)
(20457573, 79995003)
(20534278, 79995003)
(20690061, 79995003)
(21442453, 79995003)
(21649784, 79995003)
(26243046, 79995003)
(27999585, 79995003)
(24916370, 79995004)
(28284412, 79995004)
(25261126, 79995005)
(25952632, 79995005)
(29853108, 79995019)
(21116581, 79995021)
(26708460, 79995023)
(29680500, 79995043)
(23713594, 79995062)
(20554627, 79995069)
(22545518, 79995071)
(27729407, 79995071)
(29687562, 79995071)
(20653209, 79995085)
(22964572, 79995085)
(23852921, 79995085)
(24117267, 79995093)
(27749119, 79

(28504865, 80004421)
(23410341, 80004428)
(24994103, 80004428)
(28000976, 80004428)
(26167683, 80004482)
(24543506, 80004483)
(21279320, 80004502)
(23281956, 80004502)
(26643227, 80004502)
(22410277, 80004512)
(23950608, 80004524)
(29005689, 80004524)
(29673627, 80004524)
(23667545, 80004526)
(22947112, 80004533)
(23285941, 80004533)
(22956285, 80004535)
(22577904, 80004538)
(26012269, 80004539)
(23840419, 80004543)
(23375712, 80004545)
(27723968, 80004545)
(21721895, 80004551)
(22878514, 80004551)
(23028204, 80004551)
(23337185, 80004551)
(27621609, 80004551)
(23729213, 80004556)
(24827877, 80004556)
(27409146, 80004556)
(24548572, 80004558)
(20219708, 80004562)
(27049654, 80004562)
(27179829, 80004562)
(24093618, 80004563)
(23691150, 80004567)
(25754491, 80004570)
(28769452, 80004575)
(24714321, 80004578)
(27790082, 80004578)
(24684284, 80004579)
(20248360, 80004589)
(21822804, 80004589)
(24329845, 80004589)
(20025200, 80004600)
(23197517, 80004646)
(22332837, 80004648)
(23659982, 80

(29478774, 80015501)
(29558161, 80015501)
(29643901, 80015501)
(29863340, 80015501)
(29877660, 80015501)
(29885149, 80015501)
(25140231, 80015506)
(28798801, 80015506)
(23807973, 80015512)
(21908986, 80015520)
(22878436, 80015520)
(26722294, 80015520)
(29202319, 80015520)
(29210463, 80015520)
(29286177, 80015520)
(29382967, 80015520)
(29632270, 80015520)
(29695092, 80015520)
(29771544, 80015520)
(20566923, 80015555)
(24778842, 80015557)
(26119184, 80015557)
(27275677, 80015557)
(28808558, 80015557)
(23500328, 80015562)
(23997296, 80015562)
(29374364, 80015562)
(29648528, 80015562)
(29783701, 80015562)
(27459973, 80015564)
(29372939, 80015564)
(23776709, 80015572)
(27394868, 80015592)
(23571105, 80015595)
(21329128, 80015598)
(21345530, 80015598)
(23273622, 80015598)
(25444387, 80015598)
(27134111, 80015598)
(22379344, 80015607)
(24759572, 80015607)
(25390400, 80015607)
(27697548, 80015629)
(24517345, 80015644)
(23493402, 80015647)
(23514378, 80015649)
(24271336, 80015653)
(24517343, 80

(22926774, 80024129)
(22408099, 80024138)
(28312591, 80024142)
(26071312, 80024150)
(26170111, 80024150)
(27792268, 80024151)
(28877319, 80024151)
(22539828, 80024158)
(28181026, 80024158)
(22411124, 80024177)
(29014997, 80024180)
(24361287, 80024184)
(24775150, 80024187)
(24331418, 80024190)
(24360216, 80024190)
(26620360, 80024190)
(20087188, 80024205)
(22583439, 80024205)
(29088655, 80024205)
(29615773, 80024206)
(21827994, 80024257)
(23752380, 80024257)
(29274806, 80024257)
(29396148, 80024264)
(28170227, 80024266)
(23511182, 80024274)
(24119772, 80024275)
(26655708, 80024275)
(20679452, 80024277)
(28247161, 80024277)
(28944698, 80024277)
(22592014, 80024280)
(23013162, 80024283)
(25854810, 80024283)
(29432153, 80024283)
(22561784, 80024289)
(29683242, 80024290)
(20694999, 80024291)
(24555227, 80024291)
(27872780, 80024293)
(24566324, 80024322)
(21365874, 80024325)
(26741731, 80024334)
(27650862, 80024334)
(28255371, 80024334)
(28475048, 80024339)
(23674302, 80024379)
(28207027, 80

...

(28175577, 80982679)
(24032951, 80982684)
(27768597, 80982702)
(26199736, 80982715)
(24240191, 80982747)
(26120920, 80982747)
(23851901, 80982754)
(29405756, 80982754)
(24082100, 80982757)
(27953037, 80982757)
(28051067, 80982758)
(21114123, 80982760)
(29569939, 80982761)
(24545331, 80982771)
(24023456, 80982780)
(23504141, 80982789)
(23195310, 80982799)
(21021743, 80982812)
(23744910, 80982812)
(24060154, 80982812)
(22825858, 80982813)
(24740949, 80982817)
(25940191, 80982817)
(26053892, 80982817)
(28334684, 80982822)
(23995271, 80982832)
(28813440, 80982832)
(29397491, 80982836)
(21968954, 80982837)
(23482869, 80982837)
(23154421, 80982842)
(22374584, 80982846)
(24030662, 80982846)
(24085623, 80982852)
(24673046, 80982852)
(27201055, 80982852)
(22379134, 80982857)
(24078629, 80982857)
(29096641, 80982857)
(22812322, 80982861)
(28094080, 80982876)
(20596606, 80982890)
(27045263, 80982894)
(27089987, 80982894)
(23500323, 80982897)
(22600434, 80982900)
(22635574, 80982900)
(23409438, 80

(27720989, 80993500)
(21730936, 80993503)
(29748492, 80993503)
(27600130, 80993515)
(23147192, 80993534)
(24623855, 80993534)
(25256534, 80993540)
(28519554, 80993540)
(27984383, 80993544)
(23700564, 80993545)
(28786806, 80993550)
(23908921, 80993552)
(23948505, 80993611)
(22595313, 80993612)
(25348571, 80993612)
(28703480, 80993612)
(22098972, 80993621)
(26015178, 80993633)
(24778683, 80993642)
(21212695, 80993684)
(26022691, 80993703)
(27590002, 80993731)
(27775365, 80993731)
(28620268, 80993731)
(20079388, 80993741)
(24618270, 80993741)
(28677430, 80993748)
(22236495, 80993753)
(26298412, 80993753)
(29406044, 80993753)
(29678389, 80993756)
(27938282, 80993765)
(28711458, 80993765)
(22836220, 80993766)
(22859125, 80993766)
(26264834, 80993766)
(28857644, 80993766)
(22551729, 80993772)
(21073967, 80993778)
(27783545, 80993779)
(29086482, 80993785)
(22228860, 80993793)
(28337302, 80993806)
(21923485, 80993815)
(28752710, 80993815)
(23258221, 80993821)
(25902918, 80993827)
(24074050, 80

(26858431, 81003853)
(27249346, 81003853)
(20255960, 81003856)
(20161706, 81003864)
(26333168, 81003864)
(21722637, 81003908)
(26550608, 81003908)
(20531744, 81003929)
(23251101, 81003930)
(24080069, 81003938)
(22009181, 81003943)
(25730116, 81003950)
(28775520, 81003954)
(20970151, 81003962)
(23684867, 81003962)
(24943174, 81003962)
(27811306, 81003962)
(22594756, 81003965)
(23069997, 81003965)
(23511091, 81003991)
(20448126, 81003998)
(22939823, 81004013)
(27986585, 81004016)
(23474843, 81004028)
(22391497, 81004029)
(23186337, 81004029)
(23216984, 81004029)
(25217114, 81004029)
(28465514, 81004029)
(24451530, 81004035)
(27689837, 81004035)
(22559207, 81004039)
(24185892, 81004045)
(29339206, 81004054)
(22944383, 81004057)
(23619611, 81004059)
(22736264, 81004071)
(23501058, 81004073)
(29094667, 81004073)
(24332127, 81004081)
(20905284, 81004096)
(22250517, 81004096)
(28034394, 81004096)
(23112816, 81004100)
(24718703, 81004106)
(28032440, 81004117)
(25780478, 81004121)
(22719979, 81

(25104998, 81014610)
(24551378, 81014614)
(22714377, 81014623)
(20836823, 81014626)
(22587144, 81014626)
(23215233, 81014626)
(24012346, 81014626)
(20098203, 81014637)
(20815440, 81014637)
(21320860, 81014637)
(21630778, 81014637)
(25310121, 81014637)
(27300677, 81014637)
(27733293, 81014640)
(24523347, 81014651)
(24106426, 81014653)
(20055923, 81014655)
(20244730, 81014655)
(21133860, 81014655)
(23012377, 81014669)
(20066771, 81014674)
(21163169, 81014674)
(21379326, 81014674)
(26145494, 81014674)
(29409514, 81014693)
(29687765, 81014695)
(29098520, 81014713)
(23170590, 81014736)
(29234555, 81014755)
(25558961, 81014761)
(25997503, 81014761)
(20631672, 81014768)
(21229421, 81014779)
(20613547, 81014784)
(23630624, 81014784)
(24021034, 81014785)
(24528022, 81014785)
(26614353, 81014788)
(27366819, 81014795)
(23271270, 81014800)
(23747658, 81014800)
(20298713, 81014801)
(28465657, 81014804)
(20569641, 81014822)
(20128333, 81014842)
(24141499, 81014842)
(21352450, 81014843)
(26969918, 81

KeyboardInterrupt: 